# Strip Detector

<center>
<img src="icon-fig.png" width=49%/>
</center>

## Procedure (<a href=notebook.ipynb>This notebook to download</a>)<br>
<a href=StripDetector.sh>bash wrapper</a>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import re

shot_no = 33813


Download logfile and time of plasma start and plasma end

In [ ]:
log_URL = "http://golem.fjfi.cvut.cz/shots/{}/Diagnostics/StripDetector/PH32.log"
plasma_URL = "http://golem.fjfi.cvut.cz/shots/{}/analysis_wave_0/BasicDiagnostics/{}"

ds = np.DataSource(None)

#logfile = ds.open(log_URL.format(shot_no))
logfile = ds.open("PH32.log")
t_plasma_start = ds.open(plasma_URL.format(shot_no, "t_plasma_start"))
t_plasma_start = np.loadtxt(t_plasma_start)

t_plasma_end = ds.open(plasma_URL.format(shot_no, "t_plasma_end"))
t_plasma_end = np.loadtxt(t_plasma_end)

### Reading log file
first part contains information about configuration   
we need
     - acquisition time of one frame
     - delay between frames
     - acquisition mode 
         - hit count -- # of detected particles
         - ToT = Time over threshold $\sim$ deposited energy
         - first hit $\sim$ deposited energy of firts detected particle
         - ToA = Time of Arrival (for time of flight measeruement, not useful in our convtext)

second part consists of 200 frames in format: "$FRAME,*\[measured value 0-65535\]*,*\[...\]*,*\[...\]*\**checksum*    
0-65534 are used for measeured values, 65535 is used in case of overflow, channel saturation or when channel is disabled

In [ ]:
PH32_frames = []
for line in logfile:
    regex_seatm = re.match("\$ACKNL,SEATM -- acquisition time set to (\d+)us", line)
    if regex_seatm:
        acc_time = regex_seatm.group(1)
        acc_time = int(acc_time)/1000.0
            
    regex_delay = re.match("\$ACKNL,DELAY -- delay set to (\d+)us", line)
    if regex_delay:
        delay = regex_delay.group(1)
        delay = int(delay)/1000.0
            
    regex_selo1= re.match(
        "\$ACKNL,SELO1 -- local configuration for channel (\d+) was set to value (\d+)", line)
    if regex_selo1 and ( int(regex_selo1.group(2)) & 0x40):
        acc_mode = "ToT"
    elif regex_selo1 and ( int(regex_selo1.group(2)) & 0x20):
        acc_mode = "first hit"
    elif regex_selo1 and ( int(regex_selo1.group(2)) & 0x60):
        acc_mode = "ToA"
    else:
        acc_mode = "hit count"
            
    regex_startb = re.match("\$STARB,(\d+),(\d+)", line)
    if regex_startb:
        start_delay = regex_startb.group(2)
        start_delay = int(start_delay)/1000.0
                        

    regex_frame = re.match("\$FRAME,((?:\d+,)+)(\d+)\*[0-9a-f]{2}", line)
    if regex_frame:
        line = np.fromstring(''.join(regex_frame.groups()), sep=',')
        line[line == 65535] = -1 ### SATURATION or ERROR in measeurement (or chanel disabled)
        PH32_frames.append(line)
            
PH32_frames = np.array(PH32_frames)

### Rearrange channels
order of channels dont correnspod to order of strip on sensor, we need to rearange them   
strip n. 0 is on channel 15, strip n. 1 on channel 16 ... 

In [ ]:
channelOrder = [15,16,14,17,13,18,12,19,11,20,10,21,9,22,8,23,24,7,25,6,26,5,27,4,28,3,29,2,30,1,31,0]

perm_mat = np.zeros((len(channelOrder), len(channelOrder)))

for idx, i in enumerate(channelOrder):
    perm_mat[i, idx] = 1

PH32_frames = np.dot(PH32_frames, perm_mat)

### Plot result

In [ ]:
time_btw_frames = acc_time + delay
y_tics = np.arange(0,32,1)
t_tics = np.arange(0, PH32_frames.shape[0]*time_btw_frames, time_btw_frames)
t_tics += start_delay

cmap = plt.cm.get_cmap()
cmap.set_under("grey") #bad measeurement in grey


fig,ax = plt.subplots()
im = ax.pcolormesh(t_tics, y_tics, PH32_frames.T, vmin = 0, cmap=cmap)
ax.set_ylabel("strip n.")
ax.set_xlabel("time [ms]")

if t_plasma_start != -1.0 and t_plasma_start != -1.0:
    ax.set_xlim(start_delay, t_plasma_end + 2)
    ax.axvline(t_plasma_start, color = "white", dashes=[1, 2], label='plasma start')
    ax.axvline(t_plasma_end, color = "white", dashes=[1, 2], label='plasma end')

cbar = fig.colorbar(im, ax=ax);
cbar.set_label(acc_mode)

fig.savefig('icon-fig.png')